# Import

In [1]:
! pip install xgboost
! pip install lightgbm

In [2]:
import os
import numpy as np
import pandas as pd
import random

from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import (
    accuracy_score,
    classification_report,
    confusion_matrix,
    f1_score,
    precision_score,
    recall_score,
)
from sklearn.model_selection import train_test_split, StratifiedKFold
from sklearn.preprocessing import StandardScaler

from tqdm import tqdm
import matplotlib.pyplot as plt
import seaborn as sns


# Catboost model
from catboost import CatBoostClassifier, Pool

# Optuna
import optuna
from optuna import Trial
from optuna.samplers import TPESampler

import itertools

# Seed 고정
def seed_everything(seed):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)
seed_everything(42)

pd.set_option('display.max_columns', None)
# pd.set_option('display.max_rows', None)

# 데이터 불러오기

In [3]:
ROOT_DIR = "data"
RANDOM_STATE = 110
pd.set_option('display.max_columns', None)
# Load data
train_df = pd.read_csv(os.path.join(ROOT_DIR, "train.csv"))
train_data = pd.read_csv(os.path.join(ROOT_DIR, "train.csv"))
test_df = pd.read_csv(os.path.join(ROOT_DIR, "test.csv"))

In [4]:
train_df

Wip Line_Dam Process Desc._Dam     Equipment_Dam Model.Suffix_Dam  \
0          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334505   
1          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334505   
2          IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
3          IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
4          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
...            ...               ...               ...              ...   
40501      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
40502      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
40503      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
40504      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
40505      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   

      Workorder_Dam  Insp. Seq No._Dam Insp Judge Code_Dam  \
0        4F1XA938-1                  1                  OK   
1        3KPM0016-2                  1                  OK   
2        4E1X9167-1                  1                  OK   
3        3K1X0057-1                  1                  OK   
4        3HPM0007-1                  1                  OK   
...             ...                ...                 ...   
40501    3J1XF434-2                  1                  OK   
40502    4E1XC796-1                  1                  OK   
40503    4C1XD438-1                  1                  OK   
40504    3I1XA258-1                  1                  OK   
40505    3G1XA501-1                  1                  OK   

       CURE END POSITION X Collect Result_Dam  \
0                                       240.0   
1                                       240.0   
2                                      1000.0   
3                                      1000.0   
4                                       240.0   
...                                       ...   
40501                                   240.0   
40502                                  1000.0   
40503                                   240.0   
40504                                  1000.0   
40505                                   240.0   

       CURE END POSITION X Unit Time_Dam  CURE END POSITION X Judge Value_Dam  \
0                                    NaN                                  NaN   
1                                    NaN                                  NaN   
2                                    NaN                                  NaN   
3                                    NaN                                  NaN   
4                                    NaN                                  NaN   
...                                  ...                                  ...   
40501                                NaN                                  NaN   
40502                                NaN                                  NaN   
40503                                NaN                                  NaN   
40504                                NaN                                  NaN   
40505                                NaN                                  NaN   

       CURE END POSITION Z Collect Result_Dam  \
0                                         2.5   
1                                         2.5   
2                                        12.5   
3                                        12.5   
4                                         2.5   
...                                       ...   
40501                                     2.5   
40502                                    12.5   
40503                                     2.5   
40504                                    12.5   
40505                                     2.5   

       CURE END POSITION Z Unit Time_Dam  CURE END POSITION Z Judge Value_Dam  \
0                                    NaN                                  NaN   
1                                    NaN       

In [5]:
print(train_df['WorkMode Collect Result_Dam'].value_counts())
print(train_df['WorkMode Collect Result_Fill1'].value_counts())
print(train_df['WorkMode Collect Result_Fill2'].value_counts())


WorkMode Collect Result_Dam
 0.000    18972
 7.000    16447
-0.118     1649
 0.012     1347
-0.026      964
 0.007      884
 0.003      125
 0.024      118
Name: count, dtype: int64
WorkMode Collect Result_Fill1
1     22829
7     16447
6       983
9        96
17       86
3        64
4         1
Name: count, dtype: int64
WorkMode Collect Result_Fill2
1     22830
0     16447
6       983
9        96
17       86
3        64
Name: count, dtype: int64


In [6]:


# 기존 데이터프레임에서 'Equipment_Dam', 'Equipment_AutoClave', 'Equipment_Fill1', 'Equipment_Fill2' 칼럼 추출
modelsuffix_columns = ['Model.Suffix_Dam', 'Model.Suffix_AutoClave', 'Model.Suffix_Fill1', 'Model.Suffix_Fill2']

workorder_columns = ['Workorder_Dam', 'Workorder_AutoClave', 'Workorder_Fill1', 'Workorder_Fill2']

df_modelsuffix_columns = train_data[modelsuffix_columns]
df_workorder_columns = train_data[workorder_columns]
# 각 행의 값이 모두 같은지 확인
df_modelsuffix_columns['All_Equal'] = df_modelsuffix_columns.apply(lambda row: len(set(row)) == 1, axis=1)
df_workorder_columns['All_Equal'] = df_workorder_columns.apply(lambda row: len(set(row)) == 1, axis=1)
# 결과 출력

df_modelsuffix_columns_all_equal_true = df_modelsuffix_columns['All_Equal'].all()
df_workorder_columns_all_equal_true = df_workorder_columns['All_Equal'].all()


# 결과 출력
print("Model suffix 칼럼이 모두 True인지:", df_modelsuffix_columns_all_equal_true)
print("workorder 칼럼이 모두 True인지:", df_workorder_columns_all_equal_true)


Model suffix 칼럼이 모두 True인지: True
workorder 칼럼이 모두 True인지: True


C:\Users\USER\AppData\Local\Temp\ipykernel_12828\310839607.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_modelsuffix_columns['All_Equal'] = df_modelsuffix_columns.apply(lambda row: len(set(row)) == 1, axis=1)
C:\Users\USER\AppData\Local\Temp\ipykernel_12828\310839607.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_workorder_columns['All_Equal'] = df_workorder_columns.apply(lambda row: len(set(row)) == 1, axis=1)


In [7]:
# 이름 이상한부분 변경
train_df = train_df.rename(columns={'1st Pressure 1st Pressure Unit Time_AutoClave': '1st Pressure Unit Time_AutoClave'})
test_df = test_df.rename(columns={'1st Pressure 1st Pressure Unit Time_AutoClave': '1st Pressure Unit Time_AutoClave'})

In [8]:
train_df.groupby(['Process Desc._Fill1'])['target'].value_counts()

Process Desc._Fill1  target  
Fill1 Dispenser      Normal      38156
                     AbNormal     2350
Name: count, dtype: int64

In [9]:
train_df['target'].value_counts()
# 'normal' = 38156개 'Abnormal' = 2350
# 16:1 의 비로 클래스 불균형

target
Normal      38156
AbNormal     2350
Name: count, dtype: int64

In [10]:
train_df.isnull().sum()

Wip Line_Dam                         0
Process Desc._Dam                    0
Equipment_Dam                        0
Model.Suffix_Dam                     0
Workorder_Dam                        0
                                 ...  
Receip No Judge Value_Fill2      40506
WorkMode Collect Result_Fill2        0
WorkMode Unit Time_Fill2         40506
WorkMode Judge Value_Fill2       40506
target                               0
Length: 464, dtype: int64

In [11]:
train_df

Wip Line_Dam Process Desc._Dam     Equipment_Dam Model.Suffix_Dam  \
0          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334505   
1          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334505   
2          IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
3          IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
4          IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
...            ...               ...               ...              ...   
40501      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
40502      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
40503      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   
40504      IVI-OB6     Dam Dispenser  Dam dispenser #2      AJX75334501   
40505      IVI-OB6     Dam Dispenser  Dam dispenser #1      AJX75334501   

      Workorder_Dam  Insp. Seq No._Dam Insp Judge Code_Dam  \
0        4F1XA938-1                  1                  OK   
1        3KPM0016-2                  1                  OK   
2        4E1X9167-1                  1                  OK   
3        3K1X0057-1                  1                  OK   
4        3HPM0007-1                  1                  OK   
...             ...                ...                 ...   
40501    3J1XF434-2                  1                  OK   
40502    4E1XC796-1                  1                  OK   
40503    4C1XD438-1                  1                  OK   
40504    3I1XA258-1                  1                  OK   
40505    3G1XA501-1                  1                  OK   

       CURE END POSITION X Collect Result_Dam  \
0                                       240.0   
1                                       240.0   
2                                      1000.0   
3                                      1000.0   
4                                       240.0   
...                                       ...   
40501                                   240.0   
40502                                  1000.0   
40503                                   240.0   
40504                                  1000.0   
40505                                   240.0   

       CURE END POSITION X Unit Time_Dam  CURE END POSITION X Judge Value_Dam  \
0                                    NaN                                  NaN   
1                                    NaN                                  NaN   
2                                    NaN                                  NaN   
3                                    NaN                                  NaN   
4                                    NaN                                  NaN   
...                                  ...                                  ...   
40501                                NaN                                  NaN   
40502                                NaN                                  NaN   
40503                                NaN                                  NaN   
40504                                NaN                                  NaN   
40505                                NaN                                  NaN   

       CURE END POSITION Z Collect Result_Dam  \
0                                         2.5   
1                                         2.5   
2                                        12.5   
3                                        12.5   
4                                         2.5   
...                                       ...   
40501                                     2.5   
40502                                    12.5   
40503                                     2.5   
40504                                    12.5   
40505                                     2.5   

       CURE END POSITION Z Unit Time_Dam  CURE END POSITION Z Judge Value_Dam  \
0                                    NaN                                  NaN   
1                                    NaN       

In [12]:
# 모델 서픽스 리스트 정의
model_suffix_values = ['AJX75334501', 'AJX75334502', 'AJX75334503',
                       'AJX75334505', 'AJX75334506', 'AJX75334507', 'AJX75334508']

# 대상 칼럼 정의
model_suffix_columns = ['Model.Suffix_Dam', 'Model.Suffix_AutoClave', 'Model.Suffix_Fill1', 'Model.Suffix_Fill2']

# 'model_suffix_values'를 기준으로 'target' 값의 개수 합산
result = {value: {'AbNormal': 0, 'Normal': 0} for value in model_suffix_values}

for column in model_suffix_columns:
    for value in model_suffix_values:
        count_abnormal = train_df[(train_df[column] == value) & (train_df['target'] == 'AbNormal')].shape[0]
        count_normal = train_df[(train_df[column] == value) & (train_df['target'] == 'Normal')].shape[0]
        result[value]['AbNormal'] += count_abnormal
        result[value]['Normal'] += count_normal

# 결과 출력 및 비율 계산
for value in model_suffix_values:
    abnormal_count = result[value]['AbNormal']
    normal_count = result[value]['Normal']
    total_count = abnormal_count + normal_count
    abnormal_ratio = abnormal_count / total_count if total_count != 0 else 0
    normal_ratio = normal_count / total_count if total_count != 0 else 0
    print(f"Value: {value}, AbNormal: {abnormal_count}, Normal: {normal_count}, AbNormal Ratio: {abnormal_ratio:.2f}, Normal Ratio: {normal_ratio:.2f}")

Value: AJX75334501, AbNormal: 7672, Normal: 127608, AbNormal Ratio: 0.06, Normal Ratio: 0.94
Value: AJX75334502, AbNormal: 920, Normal: 12640, AbNormal Ratio: 0.07, Normal Ratio: 0.93
Value: AJX75334503, AbNormal: 176, Normal: 472, AbNormal Ratio: 0.27, Normal Ratio: 0.73
Value: AJX75334505, AbNormal: 520, Normal: 10020, AbNormal Ratio: 0.05, Normal Ratio: 0.95
Value: AJX75334506, AbNormal: 32, Normal: 484, AbNormal Ratio: 0.06, Normal Ratio: 0.94
Value: AJX75334507, AbNormal: 72, Normal: 1168, AbNormal Ratio: 0.06, Normal Ratio: 0.94
Value: AJX75334508, AbNormal: 8, Normal: 232, AbNormal Ratio: 0.03, Normal Ratio: 0.97


# 데이터 전처리

In [13]:
# 불필요한 칼럼 제거
def drop_columns_if_exist(df, columns_to_drop):
    for column in columns_to_drop:
        if column in df.columns:
            df = df.drop(column, axis=1)
            print(f"Column '{column}' dropped.")
        else:
            print(f"Column '{column}' does not exist.")
    return df

train_df = drop_columns_if_exist(train_df, {
    'Wip Line_Dam', 'Wip Line_AutoClave', 'Wip Line_Fill1', 'Wip Line_Fill2',
    'Process Desc._Dam', 'Process Desc._AutoClave', 'Process Desc._Fill1', 'Process Desc._Fill2',
})

test_df = drop_columns_if_exist(test_df, {
    'Wip Line_Dam','Wip Line_AutoClave', 'Wip Line_Fill1', 'Wip Line_Fill2',
    'Process Desc._Dam', 'Process Desc._AutoClave', 'Process Desc._Fill1', 'Process Desc._Fill2',
})


Column 'Wip Line_AutoClave' dropped.
Column 'Wip Line_Fill1' dropped.
Column 'Wip Line_Dam' dropped.
Column 'Wip Line_Fill2' dropped.
Column 'Process Desc._Dam' dropped.
Column 'Process Desc._AutoClave' dropped.
Column 'Process Desc._Fill1' dropped.
Column 'Process Desc._Fill2' dropped.
Column 'Wip Line_AutoClave' dropped.
Column 'Wip Line_Fill1' dropped.
Column 'Wip Line_Dam' dropped.
Column 'Wip Line_Fill2' dropped.
Column 'Process Desc._Dam' dropped.
Column 'Process Desc._AutoClave' dropped.
Column 'Process Desc._Fill1' dropped.
Column 'Process Desc._Fill2' dropped.


In [14]:
# NaN값은 모두 0으로 채우기
train_df = train_df.fillna(0)
test_df = test_df.fillna(0)

In [15]:
# Set ID 지우기
test_df = test_df.drop(columns=['Set ID'])

In [16]:
# 데이터 내 "OK", "NG" 등 문자열 데이터 찾기
except_columns = {'Equipment_Dam', 'Equipment_AutoClave', 'Equipment_Fill1', 'Equipment_Fill2',
                'Model.Suffix_Dam', 'Model.Suffix_AutoClave', 'Model.Suffix_Fill1', 'Model.Suffix_Fill2',
                'Workorder_Dam', 'Workorder_AutoClave', 'Workorder_Fill1', 'Workorder_Fill2',
                'target'}
def find_string_value(df):
    string_columns = []

    for col in df.columns:
        if df[col].apply(lambda x : isinstance(x, str)).any() and col not in except_columns:
            string_columns.append(col)
            print(f"Column '{col}' contains string values")

    for col in string_columns:
        print(df[col].value_counts())

    return string_columns

# "OK" -> 1, "NG" -> 0으로 인코딩
def incording_string_value(df, string_columns):
    for col in string_columns:
        df[col] = df[col].apply(lambda x: 1 if x == "OK" else 0 if x == "NG" else x)
        df[col] = df[col].astype(float)

train_df_string_columns = find_string_value(train_df)
incording_string_value(train_df, train_df_string_columns)

test_df_string_columns = find_string_value(test_df)
incording_string_value(test_df, test_df_string_columns)

Column 'Insp Judge Code_Dam' contains string values
Column 'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam' contains string values
Column 'HEAD NORMAL COORDINATE X AXIS(Stage1) Judge Value_Dam' contains string values
Column 'Insp Judge Code_AutoClave' contains string values
Column '1st Pressure Judge Value_AutoClave' contains string values
Column '2nd Pressure Judge Value_AutoClave' contains string values
Column '3rd Pressure Judge Value_AutoClave' contains string values
Column 'Chamber Temp. Judge Value_AutoClave' contains string values
Column 'GMES_ORIGIN_INSP_JUDGE_CODE Collect Result_AutoClave' contains string values
Column 'GMES_ORIGIN_INSP_JUDGE_CODE Judge Value_AutoClave' contains string values
Column 'Insp Judge Code_Fill1' contains string values
Column 'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1' contains string values
Column 'HEAD NORMAL COORDINATE X AXIS(Stage1) Judge Value_Fill1' contains string values
Column 'Insp Judge Code_Fill2' contains string

### 유의미한 칼럼추가

#### 공정데이터에서 총 4개의 대분류가 있음. Dam, AutoClave, Fill1, Fill2가 있음. 
#### Fill1과 Fill2만 대충 추가했었는데(코딩 잘못해서 Fill1은 칼럼 이름 중복되서 적용안됨.) 오히려 점수가 높아짐
#### 왜 더 분류를 잘됬는지 파악해야됨

In [17]:
# import numpy as np
# import pandas as pd

# # 공통 함수 정의
# def process_dataframe(df):
#     #     # Dam
#     # # Dam Cure 공정 관련 거리 계산
#     # df['Cure Start to End Distance'] = np.sqrt(
#     #     (df['CURE START POSITION X Collect Result_Dam'].astype(float) - df['CURE END POSITION X Collect Result_Dam'].astype(float))**2 +
#     #     (df['CURE START POSITION Z Collect Result_Dam'].astype(float) - df['CURE END POSITION Z Collect Result_Dam'].astype(float))**2 +
#     #     (df['CURE START POSITION Θ Collect Result_Dam'].astype(float) - df['CURE END POSITION Θ Collect Result_Dam'].astype(float))**2
#     # )
#     # df['Cure Standby to Start Distance'] = np.sqrt(
#     #     (df['CURE STANDBY POSITION X Collect Result_Dam'].astype(float) - df['CURE START POSITION X Collect Result_Dam'].astype(float))**2 +
#     #     (df['CURE STANDBY POSITION Z Collect Result_Dam'].astype(float) - df['CURE START POSITION Z Collect Result_Dam'].astype(float))**2 +
#     #     (df['CURE STANDBY POSITION Θ Collect Result_Dam'].astype(float) - df['CURE START POSITION Θ Collect Result_Dam'].astype(float))**2
#     # )

#     # # Cure 속도를 사용한 추가 계산 (예시로 Cure 공정 시간 계산)
#     # df['Cure Process Time'] = df['Cure Start to End Distance'].astype(float) / df['CURE SPEED Collect Result_Dam'].astype(float)

#     # # 1. 도포 소요시간 계산
#     # df['Average Coating Time'] = df[
#     #     [
#     #         'DISCHARGED TIME OF RESIN(Stage1) Collect Result_Dam',
#     #         'DISCHARGED TIME OF RESIN(Stage2) Collect Result_Dam',
#     #         'DISCHARGED TIME OF RESIN(Stage3) Collect Result_Dam'
#     #     ]
#     # ].astype(float).mean(axis=1)

#     # # 2. 총 도포량 계산
#     # df['Total Dispense Volume'] = df[
#     #     [
#     #         'Dispense Volume(Stage1) Collect Result_Dam',
#     #         'Dispense Volume(Stage2) Collect Result_Dam',
#     #         'Dispense Volume(Stage3) Collect Result_Dam'
#     #     ]
#     # ].astype(float).sum(axis=1)

#     # # 3. 도포 효율 계산
#     # df['Dispense Efficiency (CID)'] = df['Dispense Volume(Stage1) Collect Result_Dam'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Dam'].astype(float)
#     # df['Dispense Efficiency (Seg)'] = df['Dispense Volume(Stage2) Collect Result_Dam'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Dam'].astype(float)
#     # df['Dispense Efficiency (Cluster)'] = df['Dispense Volume(Stage3) Collect Result_Dam'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Dam'].astype(float)
#     # # 4. 좌표 이동 거리 계산
#     # df['Euclidean Distance (Stage1)'] = np.sqrt(
#     #     (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Dam'].astype(float))**2 +
#     #     (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Dam'].astype(float))**2 +
#     #     (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Dam'].astype(float))**2
#     # )
#     # df['Euclidean Distance (Stage2)'] = np.sqrt(
#     #     (df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Dam'].astype(float))**2 +
#     #     (df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Dam'].astype(float))**2 +
#     #     (df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Dam'].astype(float))**2
#     # )
#     # df['Euclidean Distance (Stage3)'] = np.sqrt(
#     #     (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Dam'].astype(float))**2 +
#     #     (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Dam'].astype(float))**2 +
#     #     (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Dam'].astype(float))**2
#     # )

#     # # 5. 공정 소요시간 비율 계산
#     # df['Coating Time Ratio (CID)'] = df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Dam'].astype(float) / df['Machine Tact time Collect Result_Dam'].astype(float)
#     # df['Coating Time Ratio (Seg)'] = df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Dam'].astype(float) / df['Machine Tact time Collect Result_Dam'].astype(float)
#     # df['Coating Time Ratio (Cluster)'] = df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Dam'].astype(float) / df['Machine Tact time Collect Result_Dam'].astype(float)

#     # # AutoClave
#     # # 평균 압력 및 온도 계산
#     # df['Average Pressure'] = df[
#     #     [
#     #         '1st Pressure Collect Result_AutoClave',
#     #         '2nd Pressure Collect Result_AutoClave',
#     #         '3rd Pressure Collect Result_AutoClave'
#     #     ]
#     # ].astype(float).mean(axis=1)

#     # # 압력 및 온도 변동 계산
#     # df['Pressure Variation'] = df[
#     #     [
#     #         '1st Pressure Collect Result_AutoClave',
#     #         '2nd Pressure Collect Result_AutoClave',
#     #         '3rd Pressure Collect Result_AutoClave'
#     #     ]
#     # ].astype(float).std(axis=1)

#     # # 압력 및 온도 변화율 계산
#     # df['Pressure Change Rate (Stage 1)'] = df['1st Pressure Collect Result_AutoClave'].astype(float) / df['1st Pressure Unit Time_AutoClave'].astype(float)
#     # df['Pressure Change Rate (Stage 2)'] = df['2nd Pressure Collect Result_AutoClave'].astype(float) / df['2nd Pressure Unit Time_AutoClave'].astype(float)
#     # df['Pressure Change Rate (Stage 3)'] = df['3rd Pressure Collect Result_AutoClave'].astype(float) / df['3rd Pressure Unit Time_AutoClave'].astype(float)


#     # Fill1 칼럼
#     # 평균 도포 소요시간 계산
#     df['Average Coating Time'] = df[
#         [
#             'DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill1',
#             'DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill1',
#             'DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill1'
#         ]
#     ].astype(float).mean(axis=1)

#     # 총 도포량 계산
#     df['Total Dispense Volume'] = df[
#         [
#             'Dispense Volume(Stage1) Collect Result_Fill1',
#             'Dispense Volume(Stage2) Collect Result_Fill1',
#             'Dispense Volume(Stage3) Collect Result_Fill1'
#         ]
#     ].astype(float).sum(axis=1)

#     # 도포 효율 계산
#     df['Dispense Efficiency (CID)'] = df['Dispense Volume(Stage1) Collect Result_Fill1'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill1'].astype(float)
#     df['Dispense Efficiency (Seg)'] = df['Dispense Volume(Stage2) Collect Result_Fill1'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill1'].astype(float)
#     df['Dispense Efficiency (Cluster)'] = df['Dispense Volume(Stage3) Collect Result_Fill1'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill1'].astype(float)

#     # 공정 소요시간 비율 계산
#     df['Coating Time Ratio (CID)'] = df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill1'].astype(float) / df['Machine Tact time Collect Result_Fill1'].astype(float)
#     df['Coating Time Ratio (Seg)'] = df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill1'].astype(float) / df['Machine Tact time Collect Result_Fill1'].astype(float)
#     df['Coating Time Ratio (Cluster)'] = df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill1'].astype(float) / df['Machine Tact time Collect Result_Fill1'].astype(float)

#     # 유클리드 거리 계산
#     df['Euclidean Distance (Stage1)'] = np.sqrt(
#         (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Fill1'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Fill1'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Fill1'].astype(float))**2
#     )
#     df['Euclidean Distance (Stage2)'] = np.sqrt(
#         (df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Fill1'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Fill1'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Fill1'].astype(float))**2
#     )
#     df['Euclidean Distance (Stage3)'] = np.sqrt(
#         (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Fill1'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Fill1'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Fill1'].astype(float))**2
#     )


#     # Fill2
#     # Cure 공정 관련 거리 계산
#     df['Cure Start to End Distance'] = np.sqrt(
#         (df['CURE START POSITION X Collect Result_Fill2'].astype(float) - df['CURE END POSITION X Collect Result_Fill2'].astype(float))**2 +
#         (df['CURE START POSITION Z Collect Result_Fill2'].astype(float) - df['CURE END POSITION Z Collect Result_Fill2'].astype(float))**2 +
#         (df['CURE START POSITION Θ Collect Result_Fill2'].astype(float) - df['CURE END POSITION Θ Collect Result_Fill2'].astype(float))**2
#     )
#     df['Cure Standby to Start Distance'] = np.sqrt(
#         (df['CURE STANDBY POSITION X Collect Result_Fill2'].astype(float) - df['CURE START POSITION X Collect Result_Fill2'].astype(float))**2 +
#         (df['CURE STANDBY POSITION Z Collect Result_Fill2'].astype(float) - df['CURE START POSITION Z Collect Result_Fill2'].astype(float))**2 +
#         (df['CURE STANDBY POSITION Θ Collect Result_Fill2'].astype(float) - df['CURE START POSITION Θ Collect Result_Fill2'].astype(float))**2
#     )

#     # Cure 속도를 사용한 추가 계산 (예시로 Cure 공정 시간 계산)
#     df['Cure Process Time'] = df['Cure Start to End Distance'].astype(float) / df['CURE SPEED Collect Result_Fill2'].astype(float)

#     # 평균 도포 소요시간 계산
#     df['Average Coating Time'] = df[
#         [
#             'DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill2',
#             'DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill2',
#             'DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill2'
#         ]
#     ].astype(float).mean(axis=1)

#     # 총 도포량 계산
#     df['Total Dispense Volume'] = df[
#         [
#             'Dispense Volume(Stage1) Collect Result_Fill2',
#             'Dispense Volume(Stage2) Collect Result_Fill2',
#             'Dispense Volume(Stage3) Collect Result_Fill2'
#         ]
#     ].astype(float).sum(axis=1)

#     # 도포 효율 계산
#     df['Dispense Efficiency (CID)'] = df['Dispense Volume(Stage1) Collect Result_Fill2'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill2'].astype(float)
#     df['Dispense Efficiency (Seg)'] = df['Dispense Volume(Stage2) Collect Result_Fill2'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill2'].astype(float)
#     df['Dispense Efficiency (Cluster)'] = df['Dispense Volume(Stage3) Collect Result_Fill2'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill2'].astype(float)

#     # 공정 소요시간 비율 계산
#     df['Coating Time Ratio (CID)'] = df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill2'].astype(float) / df['Machine Tact time Collect Result_Fill2'].astype(float)
#     df['Coating Time Ratio (Seg)'] = df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill2'].astype(float) / df['Machine Tact time Collect Result_Fill2'].astype(float)
#     df['Coating Time Ratio (Cluster)'] = df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill2'].astype(float) / df['Machine Tact time Collect Result_Fill2'].astype(float)

#     # 유클리드 거리 계산
#     df['Euclidean Distance (Stage1)'] = np.sqrt(
#         (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Fill2'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Fill2'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Fill2'].astype(float))**2
#     )
#     df['Euclidean Distance (Stage2)'] = np.sqrt(
#         (df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Fill2'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Fill2'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Fill2'].astype(float))**2
#     )
#     df['Euclidean Distance (Stage3)'] = np.sqrt(
#         (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Fill2'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Fill2'].astype(float))**2 +
#         (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Fill2'].astype(float))**2
#     )

#     return df

# # df와 df에 적용
# train_df = process_dataframe(train_df)
# test_df = process_dataframe(test_df)


In [18]:
import numpy as np
import pandas as pd

# 공통 함수 정의
def process_dataframe(df):
    new_columns = {}
    # Dam
    # Dam Cure 공정 관련 거리 계산
    new_columns['Cure Start to End Distance_Dam'] = np.sqrt(
        (df['CURE START POSITION X Collect Result_Dam'].astype(float) - df['CURE END POSITION X Collect Result_Dam'].astype(float))**2 +
        (df['CURE START POSITION Z Collect Result_Dam'].astype(float) - df['CURE END POSITION Z Collect Result_Dam'].astype(float))**2 +
        (df['CURE START POSITION Θ Collect Result_Dam'].astype(float) - df['CURE END POSITION Θ Collect Result_Dam'].astype(float))**2
    )
    new_columns['Cure Standby to Start Distance_Dam'] = np.sqrt(
        (df['CURE STANDBY POSITION X Collect Result_Dam'].astype(float) - df['CURE START POSITION X Collect Result_Dam'].astype(float))**2 +
        (df['CURE STANDBY POSITION Z Collect Result_Dam'].astype(float) - df['CURE START POSITION Z Collect Result_Dam'].astype(float))**2 +
        (df['CURE STANDBY POSITION Θ Collect Result_Dam'].astype(float) - df['CURE START POSITION Θ Collect Result_Dam'].astype(float))**2
    )

    # Cure 속도를 사용한 추가 계산 (예시로 Cure 공정 시간 계산)
    new_columns['Cure Process Time_Dam'] = new_columns['Cure Start to End Distance_Dam'].astype(float) / df['CURE SPEED Collect Result_Dam'].astype(float)

    # 1. 도포 소요시간 계산
    new_columns['Average Coating Time_Dam'] = df[
        [
            'DISCHARGED TIME OF RESIN(Stage1) Collect Result_Dam',
            'DISCHARGED TIME OF RESIN(Stage2) Collect Result_Dam',
            'DISCHARGED TIME OF RESIN(Stage3) Collect Result_Dam'
        ]
    ].astype(float).mean(axis=1)

    # 2. 총 도포량 계산
    new_columns['Total Dispense Volume_Dam'] = df[
        [
            'Dispense Volume(Stage1) Collect Result_Dam',
            'Dispense Volume(Stage2) Collect Result_Dam',
            'Dispense Volume(Stage3) Collect Result_Dam'
        ]
    ].astype(float).sum(axis=1)

    # 3. 도포 효율 계산
    new_columns['Dispense Efficiency (CID)_Dam'] = df['Dispense Volume(Stage1) Collect Result_Dam'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Dam'].astype(float)
    new_columns['Dispense Efficiency (Seg)_Dam'] = df['Dispense Volume(Stage2) Collect Result_Dam'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Dam'].astype(float)
    new_columns['Dispense Efficiency (Cluster)_Dam'] = df['Dispense Volume(Stage3) Collect Result_Dam'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Dam'].astype(float)

    # 4. 좌표 이동 거리 계산
    new_columns['Euclidean Distance (Stage1)_Dam'] = np.sqrt(
        (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Dam'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Dam'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Dam'].astype(float))**2
    )
    new_columns['Euclidean Distance (Stage2)_Dam'] = np.sqrt(
        (df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Dam'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Dam'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Dam'].astype(float))**2
    )
    new_columns['Euclidean Distance (Stage3)_Dam'] = np.sqrt(
        (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Dam'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Dam'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Dam'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Dam'].astype(float))**2
    )

    # 5. 공정 소요시간 비율 계산
    new_columns['Coating Time Ratio (CID)_Dam'] = df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Dam'].astype(float) / df['Machine Tact time Collect Result_Dam'].astype(float)
    new_columns['Coating Time Ratio (Seg)_Dam'] = df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Dam'].astype(float) / df['Machine Tact time Collect Result_Dam'].astype(float)
    new_columns['Coating Time Ratio (Cluster)_Dam'] = df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Dam'].astype(float) / df['Machine Tact time Collect Result_Dam'].astype(float)

    # AutoClave
    # 평균 압력 및 온도 계산
    new_columns['Average Pressure_AutoClave'] = df[
        [
            '1st Pressure Collect Result_AutoClave',
            '2nd Pressure Collect Result_AutoClave',
            '3rd Pressure Collect Result_AutoClave'
        ]
    ].astype(float).mean(axis=1)

    # 압력 및 온도 변동 계산
    new_columns['Pressure Variation_AutoClave'] = df[
        [
            '1st Pressure Collect Result_AutoClave',
            '2nd Pressure Collect Result_AutoClave',
            '3rd Pressure Collect Result_AutoClave'
        ]
    ].astype(float).std(axis=1)

    # 압력 및 온도 변화율 계산
    new_columns['Pressure Change Rate (Stage 1)_AutoClave'] = df['1st Pressure Collect Result_AutoClave'].astype(float) / df['1st Pressure Unit Time_AutoClave'].astype(float)
    new_columns['Pressure Change Rate (Stage 2)_AutoClave'] = df['2nd Pressure Collect Result_AutoClave'].astype(float) / df['2nd Pressure Unit Time_AutoClave'].astype(float)
    new_columns['Pressure Change Rate (Stage 3)_AutoClave'] = df['3rd Pressure Collect Result_AutoClave'].astype(float) / df['3rd Pressure Unit Time_AutoClave'].astype(float)

    # Fill1 칼럼
    # 평균 도포 소요시간 계산
    new_columns['Average Coating Time_Fill1'] = df[
        [
            'DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill1',
            'DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill1',
            'DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill1'
        ]
    ].astype(float).mean(axis=1)

    # 총 도포량 계산
    new_columns['Total Dispense Volume_Fill1'] = df[
        [
            'Dispense Volume(Stage1) Collect Result_Fill1',
            'Dispense Volume(Stage2) Collect Result_Fill1',
            'Dispense Volume(Stage3) Collect Result_Fill1'
        ]
    ].astype(float).sum(axis=1)

    # 도포 효율 계산
    new_columns['Dispense Efficiency (CID)_Fill1'] = df['Dispense Volume(Stage1) Collect Result_Fill1'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill1'].astype(float)
    new_columns['Dispense Efficiency (Seg)_Fill1'] = df['Dispense Volume(Stage2) Collect Result_Fill1'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill1'].astype(float)
    new_columns['Dispense Efficiency (Cluster)_Fill1'] = df['Dispense Volume(Stage3) Collect Result_Fill1'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill1'].astype(float)

    # 공정 소요시간 비율 계산
    new_columns['Coating Time Ratio (CID)_Fill1'] = df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill1'].astype(float) / df['Machine Tact time Collect Result_Fill1'].astype(float)
    new_columns['Coating Time Ratio (Seg)_Fill1'] = df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill1'].astype(float) / df['Machine Tact time Collect Result_Fill1'].astype(float)
    new_columns['Coating Time Ratio (Cluster)_Fill1'] = df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill1'].astype(float) / df['Machine Tact time Collect Result_Fill1'].astype(float)

    # 유클리드 거리 계산
    new_columns['Euclidean Distance (Stage1)_Fill1'] = np.sqrt(
        (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Fill1'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Fill1'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Fill1'].astype(float))**2
    )
    new_columns['Euclidean Distance (Stage2)_Fill1'] = np.sqrt(
        (df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Fill1'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Fill1'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Fill1'].astype(float))**2
    )
    new_columns['Euclidean Distance (Stage3)_Fill1'] = np.sqrt(
        (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Fill1'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Fill1'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Fill1'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Fill1'].astype(float))**2
    )
    # Fill2
    # Cure 공정 관련 거리 계산
    new_columns['Cure Start to End Distance_Fill2'] = np.sqrt(
        (df['CURE START POSITION X Collect Result_Fill2'].astype(float) - df['CURE END POSITION X Collect Result_Fill2'].astype(float))**2 +
        (df['CURE START POSITION Z Collect Result_Fill2'].astype(float) - df['CURE END POSITION Z Collect Result_Fill2'].astype(float))**2 +
        (df['CURE START POSITION Θ Collect Result_Fill2'].astype(float) - df['CURE END POSITION Θ Collect Result_Fill2'].astype(float))**2
    )
    new_columns['Cure Standby to Start Distance_Fill2'] = np.sqrt(
        (df['CURE STANDBY POSITION X Collect Result_Fill2'].astype(float) - df['CURE START POSITION X Collect Result_Fill2'].astype(float))**2 +
        (df['CURE STANDBY POSITION Z Collect Result_Fill2'].astype(float) - df['CURE START POSITION Z Collect Result_Fill2'].astype(float))**2 +
        (df['CURE STANDBY POSITION Θ Collect Result_Fill2'].astype(float) - df['CURE START POSITION Θ Collect Result_Fill2'].astype(float))**2
    )

    # Cure 속도를 사용한 추가 계산 (예시로 Cure 공정 시간 계산)
    new_columns['Cure Process Time_Fill2'] = new_columns['Cure Start to End Distance_Fill2'].astype(float) / df['CURE SPEED Collect Result_Fill2'].astype(float)

    # 평균 도포 소요시간 계산
    new_columns['Average Coating Time_Fill2'] = df[
        [
            'DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill2',
            'DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill2',
            'DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill2'
        ]
    ].astype(float).mean(axis=1)

    # 총 도포량 계산
    new_columns['Total Dispense Volume_Fill2'] = df[
        [
            'Dispense Volume(Stage1) Collect Result_Fill2',
            'Dispense Volume(Stage2) Collect Result_Fill2',
            'Dispense Volume(Stage3) Collect Result_Fill2'
        ]
    ].astype(float).sum(axis=1)

    # 도포 효율 계산
    new_columns['Dispense Efficiency (CID)_Fill2'] = df['Dispense Volume(Stage1) Collect Result_Fill2'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill2'].astype(float)
    new_columns['Dispense Efficiency (Seg)_Fill2'] = df['Dispense Volume(Stage2) Collect Result_Fill2'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill2'].astype(float)
    new_columns['Dispense Efficiency (Cluster)_Fill2'] = df['Dispense Volume(Stage3) Collect Result_Fill2'].astype(float) / df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill2'].astype(float)

    # 공정 소요시간 비율 계산
    new_columns['Coating Time Ratio (CID)_Fill2'] = df['DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill2'].astype(float) / df['Machine Tact time Collect Result_Fill2'].astype(float)
    new_columns['Coating Time Ratio (Seg)_Fill2'] = df['DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill2'].astype(float) / df['Machine Tact time Collect Result_Fill2'].astype(float)
    new_columns['Coating Time Ratio (Cluster)_Fill2'] = df['DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill2'].astype(float) / df['Machine Tact time Collect Result_Fill2'].astype(float)

    # 유클리드 거리 계산
    new_columns['Euclidean Distance (Stage1)_Fill2'] = np.sqrt(
        (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Fill2'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Fill2'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Fill2'].astype(float))**2
    )
    new_columns['Euclidean Distance (Stage2)_Fill2'] = np.sqrt(
        (df['HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Fill2'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Fill2'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Fill2'].astype(float))**2
    )
    new_columns['Euclidean Distance (Stage3)_Fill2'] = np.sqrt(
        (df['HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Fill2'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Fill2'].astype(float))**2 +
        (df['HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Fill2'].astype(float) - df['HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Fill2'].astype(float))**2
    )

    return new_columns




In [19]:
# 큰 분류로 되어있는 Dam, AutoClave, Fill1, Fill2에 대한 유의미한 칼럼 추가
# 네 가지 공정의 평균 도포 소요시간
def total_process_dataframe(df):
    new_columns = {}  # 딕셔너리 초기화

    new_columns['Coating Time Consistency_total'] = df[
        ['Average Coating Time_Dam', 'Average Coating Time_Fill1', 'Average Coating Time_Fill2']
    ].std(axis=1)
    # 공정 간 총 도포량의 일관성
    new_columns['Total Dispense Volume Consistency_total'] = df[
        ['Total Dispense Volume_Dam', 'Total Dispense Volume_Fill1', 'Total Dispense Volume_Fill2']
    ].std(axis=1)
    # 각 공정에서 계산된 도포 효율을 종합
    new_columns['Total Process Efficiency_total'] = df[
        ['Dispense Efficiency (CID)_Dam', 'Dispense Efficiency (CID)_Fill1', 'Dispense Efficiency (CID)_Fill2']
    ].mean(axis=1)
    # AutoClave 공정의 압력 변화가 다른 공정의 도포 시간에 미치는 영향을 분석
    new_columns['Pressure Coating Time Correlation_total'] = df[
        ['Pressure Change Rate (Stage 1)_AutoClave', 'Average Coating Time_Dam', 'Average Coating Time_Fill1', 'Average Coating Time_Fill2']
    ].corr().iloc[0, 1:].mean()
    # 각 공정의 총 소요 시간을 합산하여 전체 공정에 소요된 시간을 계산
    new_columns['Overall Process Time_total'] = df[
        ['Machine Tact time Collect Result_Dam', 'Machine Tact time Collect Result_Fill1', 'Machine Tact time Collect Result_Fill2']
    ].sum(axis=1)
    # 각 공정의 좌표 이동 거리의 합을 계산하여 전체 공정에서의 이동 거리를 평가
    new_columns['Total Euclidean Distance_total'] = df[
        ['Euclidean Distance (Stage1)_Dam', 'Euclidean Distance (Stage1)_Fill1', 'Euclidean Distance (Stage1)_Fill2']
    ].sum(axis=1)
    # 공정 간의 일관성을 평가하기 위해 각 공정에서의 도포 소요시간과 총 도포량의 표준편차를 비교하여 일관성을 평가
    new_columns['Process Consistency_total'] = df[
        ['Average Coating Time_Dam', 'Total Dispense Volume_Dam', 'Average Coating Time_Fill1', 'Total Dispense Volume_Fill1', 'Average Coating Time_Fill2', 'Total Dispense Volume_Fill2']
    ].std(axis=1)

    return new_columns


In [20]:
# process_dataframe 함수에서 사용된 칼럼들 목록
used_columns = [
    'CURE START POSITION X Collect Result_Dam',
    'CURE END POSITION X Collect Result_Dam',
    'CURE START POSITION Z Collect Result_Dam',
    'CURE END POSITION Z Collect Result_Dam',
    'CURE START POSITION Θ Collect Result_Dam',
    'CURE END POSITION Θ Collect Result_Dam',
    'CURE STANDBY POSITION X Collect Result_Dam',
    'CURE START POSITION X Collect Result_Dam',
    'CURE STANDBY POSITION Z Collect Result_Dam',
    'CURE START POSITION Z Collect Result_Dam',
    'CURE STANDBY POSITION Θ Collect Result_Dam',
    'CURE START POSITION Θ Collect Result_Dam',
    'CURE SPEED Collect Result_Dam',
    'DISCHARGED TIME OF RESIN(Stage1) Collect Result_Dam',
    'DISCHARGED TIME OF RESIN(Stage2) Collect Result_Dam',
    'DISCHARGED TIME OF RESIN(Stage3) Collect Result_Dam',
    'Dispense Volume(Stage1) Collect Result_Dam',
    'Dispense Volume(Stage2) Collect Result_Dam',
    'Dispense Volume(Stage3) Collect Result_Dam',
    'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Dam',
    'HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Dam',
    'HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Dam',
    'HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Dam',
    'HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Dam',
    'HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Dam',
    'HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Dam',
    'HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Dam',
    'HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Dam',
    'Machine Tact time Collect Result_Dam',
    '1st Pressure Collect Result_AutoClave',
    '2nd Pressure Collect Result_AutoClave',
    '3rd Pressure Collect Result_AutoClave',
    '1st Pressure Unit Time_AutoClave',
    '2nd Pressure Unit Time_AutoClave',
    '3rd Pressure Unit Time_AutoClave',
    'DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill1',
    'DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill1',
    'DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill1',
    'Dispense Volume(Stage1) Collect Result_Fill1',
    'Dispense Volume(Stage2) Collect Result_Fill1',
    'Dispense Volume(Stage3) Collect Result_Fill1',
    'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill1',
    'HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Fill1',
    'HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Fill1',
    'HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Fill1',
    'HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Fill1',
    'HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Fill1',
    'HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Fill1',
    'HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Fill1',
    'HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Fill1',
    'Machine Tact time Collect Result_Fill1',
    'CURE START POSITION X Collect Result_Fill2',
    'CURE END POSITION X Collect Result_Fill2',
    'CURE START POSITION Z Collect Result_Fill2',
    'CURE END POSITION Z Collect Result_Fill2',
    'CURE START POSITION Θ Collect Result_Fill2',
    'CURE END POSITION Θ Collect Result_Fill2',
    'CURE STANDBY POSITION X Collect Result_Fill2',
    'CURE START POSITION X Collect Result_Fill2',
    'CURE STANDBY POSITION Z Collect Result_Fill2',
    'CURE START POSITION Z Collect Result_Fill2',
    'CURE STANDBY POSITION Θ Collect Result_Fill2',
    'CURE START POSITION Θ Collect Result_Fill2',
    'CURE SPEED Collect Result_Fill2',
    'DISCHARGED TIME OF RESIN(Stage1) Collect Result_Fill2',
    'DISCHARGED TIME OF RESIN(Stage2) Collect Result_Fill2',
    'DISCHARGED TIME OF RESIN(Stage3) Collect Result_Fill2',
    'Dispense Volume(Stage1) Collect Result_Fill2',
    'Dispense Volume(Stage2) Collect Result_Fill2',
    'Dispense Volume(Stage3) Collect Result_Fill2',
    'HEAD NORMAL COORDINATE X AXIS(Stage1) Collect Result_Fill2',
    'HEAD NORMAL COORDINATE X AXIS(Stage2) Collect Result_Fill2',
    'HEAD NORMAL COORDINATE X AXIS(Stage3) Collect Result_Fill2',
    'HEAD NORMAL COORDINATE Y AXIS(Stage1) Collect Result_Fill2',
    'HEAD NORMAL COORDINATE Y AXIS(Stage2) Collect Result_Fill2',
    'HEAD NORMAL COORDINATE Y AXIS(Stage3) Collect Result_Fill2',
    'HEAD NORMAL COORDINATE Z AXIS(Stage1) Collect Result_Fill2',
    'HEAD NORMAL COORDINATE Z AXIS(Stage2) Collect Result_Fill2',
    'HEAD NORMAL COORDINATE Z AXIS(Stage3) Collect Result_Fill2',
    'Machine Tact time Collect Result_Fill2'
]


In [21]:
# 클래스 가중치
from sklearn.utils.class_weight import compute_class_weight

classes = np.unique(train_df['target'])
weights = compute_class_weight(class_weight = 'balanced', classes = classes, y = train_df['target'])
class_weights = dict(zip(classes, weights))
class_weights

{'AbNormal': 8.618297872340426, 'Normal': 0.5307946325610651}

In [22]:
# 범주형인 열 확인
cat_cols = train_df.select_dtypes(include=['object', 'category']).columns
cat_cols

Index(['Equipment_Dam', 'Model.Suffix_Dam', 'Workorder_Dam',
       'Equipment_AutoClave', 'Model.Suffix_AutoClave', 'Workorder_AutoClave',
       'Equipment_Fill1', 'Model.Suffix_Fill1', 'Workorder_Fill1',
       'Equipment_Fill2', 'Model.Suffix_Fill2', 'Workorder_Fill2', 'target'],
      dtype='object')

In [23]:
ncat_cols = np.where(train_df.dtypes == np.float64)[0]
ncat_cols

array([  4,   5,   6,   7,   8,   9,  10,  12,  13,  15,  16,  18,  19,
        20,  21,  22,  24,  25,  27,  28,  29,  30,  31,  33,  34,  36,
        37,  38,  39,  40,  41,  42,  43,  44,  45,  46,  47,  48,  49,
        50,  51,  52,  53,  54,  55,  56,  57,  58,  59,  60,  61,  62,
        63,  64,  65,  66,  67,  68,  69,  70,  71,  72,  73,  74,  75,
        76,  77,  78,  79,  80,  81,  82,  83,  84,  85,  87,  88,  90,
        91,  92,  93,  94,  95,  96,  97,  98,  99, 100, 101, 102, 103,
       105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117,
       118, 119, 120, 121, 122, 123, 124, 126, 127, 129, 130, 132, 133,
       135, 136, 138, 139, 141, 142, 144, 145, 147, 148, 150, 151, 153,
       154, 156, 157, 159, 160, 162, 163, 165, 166, 168, 169, 171, 172,
       174, 175, 177, 178, 180, 181, 183, 184, 186, 187, 189, 190, 192,
       193, 195, 196, 198, 199, 201, 202, 204, 205, 206, 207, 208, 209,
       210, 211, 212, 213, 214, 219, 220, 222, 223, 225, 226, 22

In [24]:
# min-max scaling
from sklearn.preprocessing import MinMaxScaler
nms = MinMaxScaler()

nms.fit(train_df.iloc[:, ncat_cols])
train_df.iloc[:, ncat_cols] = nms.transform(train_df.iloc[:, ncat_cols])
test_df.iloc[:, ncat_cols] = nms.transform(test_df.iloc[:, ncat_cols])

In [74]:
train_df

Equipment_Dam Model.Suffix_Dam Workorder_Dam  Insp. Seq No._Dam  \
0      Dam dispenser #1      AJX75334505    4F1XA938-1                  1   
1      Dam dispenser #1      AJX75334505    3KPM0016-2                  1   
2      Dam dispenser #2      AJX75334501    4E1X9167-1                  1   
3      Dam dispenser #2      AJX75334501    3K1X0057-1                  1   
4      Dam dispenser #1      AJX75334501    3HPM0007-1                  1   
...                 ...              ...           ...                ...   
40501  Dam dispenser #1      AJX75334501    3J1XF434-2                  1   
40502  Dam dispenser #2      AJX75334501    4E1XC796-1                  1   
40503  Dam dispenser #1      AJX75334501    4C1XD438-1                  1   
40504  Dam dispenser #2      AJX75334501    3I1XA258-1                  1   
40505  Dam dispenser #1      AJX75334501    3G1XA501-1                  1   

       Insp Judge Code_Dam  CURE END POSITION X Collect Result_Dam  \
0                      0.0                                     0.0   
1                      0.0                                     0.0   
2                      0.0                                     1.0   
3                      0.0                                     1.0   
4                      0.0                                     0.0   
...                    ...                                     ...   
40501                  0.0                                     0.0   
40502                  0.0                                     1.0   
40503                  0.0                                     0.0   
40504                  0.0                                     1.0   
40505                  0.0                                     0.0   

       CURE END POSITION X Unit Time_Dam  CURE END POSITION X Judge Value_Dam  \
0                                    0.0                                  0.0   
1                                    0.0                                  0.0   
2                                    0.0                                  0.0   
3                                    0.0                                  0.0   
4                                    0.0                                  0.0   
...                                  ...                                  ...   
40501                                0.0                                  0.0   
40502                                0.0                                  0.0   
40503                                0.0                                  0.0   
40504                                0.0                                  0.0   
40505                                0.0                                  0.0   

       CURE END POSITION Z Collect Result_Dam  \
0                                         0.0   
1                                         0.0   
2                                         1.0   
3                                         1.0   
4                                         0.0   
...                                       ...   
40501                                     0.0   
40502                                     1.0   
40503                                     0.0   
40504                                     1.0   
40505                                     0.0   

       CURE END POSITION Z Unit Time_Dam  CURE END POSITION Z Judge Value_Dam  \
0                                    0.0                                  0.0   
1                                    0.0                                  0.0   
2                                    0.0                                  0.0   
3                                    0.0                                  0.0   
4                                    0.0                                  0.0   
...                                  ...                                  ...   
40501                                0.0                                  0.0   
40502                             

# 레이블 인코딩

In [ ]:
from sklearn.preprocessing import LabelEncoder

# 'Abnormal' = 0, 'normal' = 1

# case 1 범주형으로 생각되는 칼럼 모두 범주형
qual_col = [
            'Equipment_Dam', 'Equipment_AutoClave', 'Equipment_Fill1', 'Equipment_Fill2',
            'Model.Suffix_Dam', 'Model.Suffix_AutoClave', 'Model.Suffix_Fill1', 'Model.Suffix_Fill2',
            'Workorder_Dam', 'Workorder_AutoClave', 'Workorder_Fill1', 'Workorder_Fill2',
            'target']

for i in qual_col:
    le = LabelEncoder()
    le = le.fit(train_df[i])
    train_df[i] = le.transform(train_df[i])

    if not i == 'target':
        for label in np.unique(test_df[i]):
            if label not in le.classes_ :
                le.classes_ = np.append(le.classes_, label)
        test_df[i] = le.transform(test_df[i])


In [24]:
# NaN값은 모두 0으로 채우기
train_df = train_df.fillna(0)
test_df = test_df.fillna(0)

# 'target' 칼럼을 잘라서 맨 뒤에 붙이는 함수
def move_target_to_end(df):
    target_col = df.pop('target')
    df['target'] = target_col
    return df

# 함수 적용
train_df = move_target_to_end(train_df)
test_df = move_target_to_end(test_df)

C:\Users\USER\AppData\Local\Temp\ipykernel_11472\4075006511.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['target'] = target_col
C:\Users\USER\AppData\Local\Temp\ipykernel_11472\4075006511.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['target'] = target_col


In [25]:
# train_df = train_df.round(1)
train_df

Equipment_Dam  Model.Suffix_Dam  Workorder_Dam  Insp. Seq No._Dam  \
0                  0                 3            657                  1   
1                  0                 3            283                  1   
2                  1                 0            589                  1   
3                  1                 0            251                  1   
4                  0                 0            142                  1   
...              ...               ...            ...                ...   
40501              0                 0            238                  1   
40502              1                 0            643                  1   
40503              0                 0            540                  1   
40504              1                 0            164                  1   
40505              0                 0             46                  1   

       Insp Judge Code_Dam  CURE END POSITION X Collect Result_Dam  \
0                        1                                   240.0   
1                        1                                   240.0   
2                        1                                  1000.0   
3                        1                                  1000.0   
4                        1                                   240.0   
...                    ...                                     ...   
40501                    1                                   240.0   
40502                    1                                  1000.0   
40503                    1                                   240.0   
40504                    1                                  1000.0   
40505                    1                                   240.0   

       CURE END POSITION X Unit Time_Dam  CURE END POSITION X Judge Value_Dam  \
0                                    0.0                                  0.0   
1                                    0.0                                  0.0   
2                                    0.0                                  0.0   
3                                    0.0                                  0.0   
4                                    0.0                                  0.0   
...                                  ...                                  ...   
40501                                0.0                                  0.0   
40502                                0.0                                  0.0   
40503                                0.0                                  0.0   
40504                                0.0                                  0.0   
40505                                0.0                                  0.0   

       CURE END POSITION Z Collect Result_Dam  \
0                                         2.5   
1                                         2.5   
2                                        12.5   
3                                        12.5   
4                                         2.5   
...                                       ...   
40501                                     2.5   
40502                                    12.5   
40503                                     2.5   
40504                                    12.5   
40505                                     2.5   

       CURE END POSITION Z Unit Time_Dam  CURE END POSITION Z Judge Value_Dam  \
0                                    0.0                                  0.0   
1                                    0.0                                  0.0   
2                                    0.0                                  0.0   
3                                    0.0                                  0.0   
4                                    0.0                                  0.0   
...                                  ...                                  ...   
40501                                0.0                                  0.0   
40502                                0.0   

In [26]:
# test_df = test_df.round(1)
test_df

Equipment_Dam  Model.Suffix_Dam  Workorder_Dam  Insp. Seq No._Dam  \
0                  1                 0            240                  1   
1                  1                 0            509                  1   
2                  0                 0            127                  1   
3                  1                 0            306                  1   
4                  0                 0            415                  1   
...              ...               ...            ...                ...   
17356              1                 0            277                  1   
17357              1                 0            439                  1   
17358              0                 0            314                  1   
17359              0                 0              8                  1   
17360              0                 0            211                  1   

       Insp Judge Code_Dam  CURE END POSITION X Collect Result_Dam  \
0                        1                                  1000.0   
1                        1                                  1000.0   
2                        1                                   240.0   
3                        1                                  1000.0   
4                        1                                   240.0   
...                    ...                                     ...   
17356                    1                                  1000.0   
17357                    1                                  1000.0   
17358                    1                                   240.0   
17359                    1                                   240.0   
17360                    1                                   240.0   

       CURE END POSITION X Unit Time_Dam  CURE END POSITION X Judge Value_Dam  \
0                                    0.0                                  0.0   
1                                    0.0                                  0.0   
2                                    0.0                                  0.0   
3                                    0.0                                  0.0   
4                                    0.0                                  0.0   
...                                  ...                                  ...   
17356                                0.0                                  0.0   
17357                                0.0                                  0.0   
17358                                0.0                                  0.0   
17359                                0.0                                  0.0   
17360                                0.0                                  0.0   

       CURE END POSITION Z Collect Result_Dam  \
0                                        12.5   
1                                        12.5   
2                                         2.5   
3                                        12.5   
4                                         2.5   
...                                       ...   
17356                                    12.5   
17357                                    12.5   
17358                                     2.5   
17359                                     2.5   
17360                                     2.5   

       CURE END POSITION Z Unit Time_Dam  CURE END POSITION Z Judge Value_Dam  \
0                                    0.0                                  0.0   
1                                    0.0                                  0.0   
2                                    0.0                                  0.0   
3                                    0.0                                  0.0   
4                                    0.0                                  0.0   
...                                  ...                                  ...   
17356                                0.0                                  0.0   
17357                                0.0   

# 언더 샘플링

In [27]:
# import pandas as pdX_MOVEMENT_DISTANCE_DAMel.Suffix_Fill1', 'Model.Suffix_Fill2']

# # 'Normal' 및 'AbNormal' 데이터 분리
# df_normal = train_df[train_df["target"] == 1]
# df_abnormal = train_df[train_df["target"] == 0]

# # 각 모델 서픽스 값에 대해 AbNormal 개수를 기준으로 Normal 데이터 샘플링
# normal_samples = []

# for value in model_suffix_values:
#     # 각 모델 서픽스 값에 대해 조건을 만족하는 데이터 선택
#     abnormal_subset = df_abnormal[df_abnormal[model_suffix_columns].isin([value]).any(axis=1)]
#     normal_subset = df_normal[df_normal[model_suffix_columns].isin([value]).any(axis=1)]

#     if not normal_subset.empty:
#         # 샘플링 크기 설정
#         sample_size = len(abnormal_subset)
#         sample_size = min(sample_size, len(normal_subset))  # 샘플링 크기가 원본 데이터 크기보다 크지 않도록 설정
#         sampled_normal = normal_subset.sample(n=sample_size, replace=False, random_state=42)
#         normal_samples.append(sampled_normal)
#     else:
#         print(f"No data found for model suffix value: {value}")

# # 샘플링된 'Normal' 데이터 결합
# if normal_samples:
#     df_normal_sampled = pd.concat(normal_samples, axis=0)
# else:
#     df_normal_sampled = pd.DataFrame()

# # 언더샘플링된 데이터프레임 생성 (AbNormal 데이터와 샘플링된 Normal 데이터를 결합)X_MOVEMENT_DISTANCE_DAM
# if not df_normal_sampled.empty:
#     train_df = pd.concat([df_normal_sampled, df_abnormal], axis=0).reset_index(drop=True)
# else:
#     train_df= df_abnormal.copy()

# # 결과 출력
# print(train_df['target'].value_counts())

# # 샘플링된 데이터에서 'model_suffix_values'를 기준으로 'target' 값의 개수 합산
# result = {value: {'AbNormal': 0, 'Normal': 0} for value in model_suffix_values}

# for value in model_suffix_values:
#     # 각 서픽스 값에 대해 AbNormal 및 Normal 데이터 개수 계산
#     abnormal_count = train_df[(train_df[model_suffix_columns].isin([value]).any(axis=1)) & (train_df['target'] == 0)].shape[0]
#     normal_count = train_df[(train_df[model_suffix_columns].isin([value]).any(axis=1)) & (train_df['target'] == 1)].shape[0]
#     result[value]['AbNormal'] += abnormal_count
#     result[value]['Normal'] += normal_count

# # 결과 출력 및 비율 계산
# for value in model_suffix_values:
#     abnormal_count = result[value]['AbNormal']
#     normal_count = result[value]['Normal']
#     total_count = abnormal_count + normal_count
#     abnormal_ratio = abnormal_count / total_count if total_count != 0 else 0
#     normal_ratio = normal_count / total_count if total_count != 0 else 0
#     print(f"Value: {value}, AbNormal: {abnormal_count}, Normal: {normal_count}, AbNormal Ratio: {abnormal_ratio:.2f}, Normal Ratio: {normal_ratio:.2f}")


# 하이퍼파라미터 튜닝

### 최적의 하이퍼파라미터 찾기

In [27]:
# 유의미한 칼럼을 추가하기 전의 baseline metric 계산

def calculate_metrics(x, y, cat_features):
    all_metrics = []
    for train_idx, valid_idx in skf.split(x, y):
        train_df = x.iloc[train_idx]
        x_valid = x.iloc[valid_idx]
        y_train = y.iloc[train_idx]
        y_valid = y.iloc[valid_idx]

        cbc.fit(x_train, y_train, cat_features=cat_features, eval_set=(x_valid, y_valid), early_stopping_rounds=100)
        cbc_result += cbc.predict_proba(test_df)/10

        y_pred = cbc.predict(x_valid)
        y_pred_proba = cbc.predict_proba(x_valid)[:, 1]

        # 다양한 지표 계산
        accuracy = accuracy_score(y_valid, y_pred)
        precision = precision_score(y_valid, y_pred, pos_label=0)
        recall = recall_score(y_valid, y_pred, pos_label=0)
        f1 = f1_score(y_valid, y_pred, pos_label=0)

        metrics = {
            'accuracy': accuracy,
            'precision': precision,
            'recall': recall,
            'f1_score': f1
        }
        all_metrics.append(metrics)

    # 평균 지표 계산 및 출력
    average_metrics = {
        'accuracy': np.mean([metrics['accuracy'] for metrics in all_metrics]),
        'precision': np.mean([metrics['precision'] for metrics in all_metrics]),
        'recall': np.mean([metrics['recall'] for metrics in all_metrics]),
        'f1_score': np.mean([metrics['f1_score'] for metrics in all_metrics]),
    }

    return average_metrics


In [29]:
# import numpy as np
# import pandas as pd
# from sklearn.metrics import confusion_matrix, precision_score, recall_score, accuracy_score, f1_score
# from catboost import CatBoostClassifier
# from sklearn.model_selection import StratifiedKFold

# def objective(Trial):
#     cbc_param = {
#         'random_state':42,
#         'iterations':Trial.suggest_int('iterations', 1000, 20000),
#         'learning_rate':Trial.suggest_uniform('learning_rate', 0.01, 0.1),
#         'bagging_temperature':Trial.suggest_loguniform('bagging_temperature', 0.01, 100.00),
#         'n_estimators':Trial.suggest_int('n_estimators',1000, 10000),
#         'max_depth':Trial.suggest_int('max_depth', 4, 16),
#         'random_strength':Trial.suggest_int('random_strength', 0, 100),
#         'colsample_bylevel':Trial.suggest_float('colsample_bylevel', 0.4, 1.0),
#         'l2_leaf_reg':Trial.suggest_float('l2_leaf_reg',1e-8,3e-5),
#         'min_child_samples': Trial.suggest_int('min_child_samples', 5, 100),
#         'max_bin': Trial.suggest_int('max_bin', 200, 500),
#         'od_type': Trial.suggest_categorical('od_type', ['IncToDec', 'Iter'])
#     }

#     x = train_dfdrop(columns=['target'])
#     y = train_df['target']

#     x_train, x_val, y_train, y_val = train_test_split(x, y, test_size = 0.2)

#     cat_features = [
#         'Equipment_Dam', 'Equipment_AutoClave', 'Equipment_Fill1', 'Equipment_Fill2',
#         'Model.Suffix_Dam', 'Model.Suffix_AutoClave', 'Model.Suffix_Fill1', 'Model.Suffix_Fill2',
#         'Workorder_Dam', 'Workorder_AutoClave', 'Workorder_Fill1', 'Workorder_Fill2',
#         # 'Chamber Temp. Judge Value_AutoClave'
#     ]

#     cbc = CatBoostClassifier(**cbc_param)

#     skf = StratifiedKFold(n_splits=10, shuffle=True, random_state=42)

#     # 언더 샘플링한 데이터
#     x = train_df.drop(columns=['target'])
#     y = train_df['target']

#     cbc_result = 0
#     feature_importance = 0
#     all_metrics = []

#     for train_idx, valid_idx in skf.split(x, y):
#         x_train = x.iloc[train_idx]
#         x_valid = x.iloc[valid_idx]
#         y_train = y.iloc[train_idx]
#         y_valid = y.iloc[valid_idx]

#         cbc.fit(x_train, y_train, cat_features=cat_features, eval_set=(x_valid, y_valid), early_stopping_rounds=100)
#         cbc_result += cbc.predict_proba(test_df)/10
#         feature_importance += cbc.feature_importances_/10

#         # 검증 데이터 예측
#         y_pred = cbc.predict(x_valid)
#         y_pred_proba = cbc.predict_proba(x_valid)[:, 1]

#         # 다양한 지표 계산
#         accuracy = accuracy_score(y_valid, y_pred)
#         precision = precision_score(y_valid, y_pred, pos_label=0)
#         recall = recall_score(y_valid, y_pred, pos_label=0)
#         f1 = f1_score(y_valid, y_pred, pos_label=0)

#         # 혼동 행렬
#         conf_matrix = confusion_matrix(y_valid, y_pred)

#         metrics = {
#         'accuracy': accuracy,
#         'precision': precision,
#         'recall': recall,
#         'f1_score': f1,
#         'confusion_matrix': conf_matrix
#         }

In [30]:
# sampler = TPESampler(seed=42)
# study = optuna.create_study(sampler=sampler)
# study.optimize(objective, n_trials=10)
# print("Best Score:",study.best_value)
# print("Best trial:",study.best_trial.params)

# CatBoostClassifier

In [31]:
import numpy as np
import pandas as pd
from sklearn.metrics import confusion_matrix, precision_score, recall_score, accuracy_score, f1_score
from catboost import CatBoostClassifier
from sklearn.model_selection import StratifiedKFold

# 범주형 특징 열을 정의
cat_features = [
    'Equipment_Dam', 'Equipment_AutoClave', 'Equipment_Fill1', 'Equipment_Fill2',
    'Model.Suffix_Dam', 'Model.Suffix_AutoClave', 'Model.Suffix_Fill1', 'Model.Suffix_Fill2',
    'Workorder_Dam', 'Workorder_AutoClave', 'Workorder_Fill1', 'Workorder_Fill2',
    # 'Chamber Temp. Judge Value_AutoClave'
]

# CatBoostClassifier 설정
cbc = CatBoostClassifier(
    iterations=2000,
    learning_rate=0.01,
    depth=7,
    verbose=100,
    grow_policy='Lossguide',
    score_function='Cosine',
    task_type='CPU'
)

# Stratified K-Fold 설정
skf = StratifiedKFold(n_splits=10, shuffle=True, random_state=42)

# 언더 샘플링한 데이터
x = train_df.drop(columns=['target'])
y = train_df['target']

cbc_result = 0
feature_importance = 0
all_metrics = []

# 유의미한 칼럼을 추가하기 전의 baseline metric 계산
# Baseline metric 계산
baseline_metrics = calculate_metrics(x, y, cat_features)

# 유의미한 칼럼 추가 (예시로 train_df와 test_df에 추가한 경우)
train_df = pd.concat([train_df, pd.DataFrame(process_dataframe(train_df))], axis=1)
test_df = pd.concat([test_df, pd.DataFrame(process_dataframe(test_df))], axis=1)
train_df = pd.concat([train_df, pd.DataFrame(total_process_dataframe(train_df))], axis=1)
test_df = pd.concat([test_df, pd.DataFrame(total_process_dataframe(test_df))], axis=1)

# # 해당 칼럼들을 train_df와 test_df에서 삭제
# train_df.drop(columns=used_columns, inplace=True)
# test_df.drop(columns=used_columns, inplace=True)

# NaN값은 모두 0으로 채우기
train_df = train_df.fillna(0)
test_df = test_df.fillna(0)

# target칼럼 맨뒤로 이동 함수 적용
train_df = move_target_to_end(train_df)
test_df = move_target_to_end(test_df)

# train_df = train_df.round(2)
# test_df = test_df.round(2)

new_metrics = calculate_metrics(x, y, cat_features)

# Metric이 증가한 경우의 칼럼 확인
improved_columns = []

if new_metrics['accuracy'] > baseline_metrics['accuracy']:
    improved_columns.append('Accuracy')

if new_metrics['precision'] > baseline_metrics['precision']:
    improved_columns.append('Precision')

if new_metrics['recall'] > baseline_metrics['recall']:
    improved_columns.append('Recall')

if new_metrics['f1_score'] > baseline_metrics['f1_score']:
    improved_columns.append('F1 Score')

# 증가한 경우의 칼럼 출력
print("Metrics improved for columns:", improved_columns)

for train_idx, valid_idx in skf.split(x, y):
    x_train = x.iloc[train_idx]
    x_valid = x.iloc[valid_idx]
    y_train = y.iloc[train_idx]
    y_valid = y.iloc[valid_idx]

    cbc.fit(x_train, y_train, class_weights=class_weights, cat_features=cat_features, eval_set=(x_valid, y_valid), early_stopping_rounds=100)
    cbc_result += cbc.predict_proba(test_df)/10
    feature_importance += cbc.feature_importances_/10

    # 검증 데이터 예측
    y_pred = cbc.predict(x_valid)
    y_pred_proba = cbc.predict_proba(x_valid)[:, 1]

    # 다양한 지표 계산
    accuracy = accuracy_score(y_valid, y_pred)
    precision = precision_score(y_valid, y_pred, pos_label=0)
    recall = recall_score(y_valid, y_pred, pos_label=0)
    f1 = f1_score(y_valid, y_pred, pos_label=0)

    # 혼동 행렬
    conf_matrix = confusion_matrix(y_valid, y_pred)

    metrics = {
        'accuracy': accuracy,
        'precision': precision,
        'recall': recall,
        'f1_score': f1,
        'confusion_matrix': conf_matrix
    }
    all_metrics.append(metrics)

# 결과 출력
for i, metrics in enumerate(all_metrics):
    print(f"Fold {i+1} Metrics:")
    print(f"Accuracy: {metrics['accuracy']:.4f}")
    print(f"Precision: {metrics['precision']:.4f}")
    print(f"Recall: {metrics['recall']:.4f}")
    print(f"F1 Score: {metrics['f1_score']:.4f}")
    print(f"Confusion Matrix:\n{metrics['confusion_matrix']}")
    print("\n")

# 최종 평균 지표 계산 및 출력
average_metrics = {
    'accuracy': np.mean([metrics['accuracy'] for metrics in all_metrics]),
    'precision': np.mean([metrics['precision'] for metrics in all_metrics]),
    'recall': np.mean([metrics['recall'] for metrics in all_metrics]),
    'f1_score': np.mean([metrics['f1_score'] for metrics in all_metrics]),
}

print("Average Metrics:")
print(f"Average Accuracy: {average_metrics['accuracy']:.4f}")
print(f"Average Precision: {average_metrics['precision']:.4f}")
print(f"Average Recall: {average_metrics['recall']:.4f}")
print(f"Average F1 Score: {average_metrics['f1_score']:.4f}")

# 중요 특징 출력
feature_importance_df = pd.DataFrame({
    'Feature': x.columns,
    'Importance': feature_importance
}).sort_values(by='Importance', ascending=False)

print('Feature Importances:')
print(feature_importance_df)

result = pd.DataFrame(cbc_result)

result['target'] = result.apply(lambda row: 'AbNormal' if row[0] > row[1] else 'Normal', axis=1)

# 결과 저장
submission = pd.read_csv('submission.csv')
submission['target'] = result['target']
submission.to_csv("submission.csv", index=False)

print("Prediction and submission file saved.")


0:	learn: 0.6805448	test: 0.6805908	best: 0.6805908 (0)	total: 495ms	remaining: 16m 30s


KeyboardInterrupt: 

In [ ]:
# submission.csv 파일에서 예측된 결과를 불러오기
submission = pd.read_csv('submission.csv')

# 예측 결과와 원본 데이터 결합
train_df['predicted_target'] = submission['target']

# Model.Suffix 값별로 AbNormal과 Normal
# 비율 계산
result = {value: {'AbNormal': 0, 'Normal': 0} for value in model_suffix_values}

for column in model_suffix_columns:
    for value in model_suffix_values:
        count_abnormal = train_df[(train_df[column] == value) & (train_df['predicted_target'] == 'AbNormal')].shape[0]
        count_normal = train_df[(train_df[column] == value) & (train_df['predicted_target'] == 'Normal')].shape[0]
        result[value]['AbNormal'] += count_abnormal
        result[value]['Normal'] += count_normal

# 결과 출력 및 비율 계산
print("Model Suffix Value별 AbNormal과 Normal 비율:")
for value in model_suffix_values:
    abnormal_count = result[value]['AbNormal']
    normal_count = result[value]['Normal']
    total_count = abnormal_count + normal_count
    abnormal_ratio = abnormal_count / total_count if total_count != 0 else 0
    normal_ratio = normal_count / total_count if total_count != 0 else 0
    print(f"Model Suffix Value: {value}")
    print(f"  AbNormal: {abnormal_count}, Normal: {normal_count}")
    print(f"  AbNormal Ratio: {abnormal_ratio:.2f}, Normal Ratio: {normal_ratio:.2f}")


Model Suffix Value별 AbNormal과 Normal 비율:
Model Suffix Value: 0
  AbNormal: 5336, Normal: 10008
  AbNormal Ratio: 0.35, Normal Ratio: 0.65
Model Suffix Value: 1
  AbNormal: 696, Normal: 1144
  AbNormal Ratio: 0.38, Normal Ratio: 0.62
Model Suffix Value: 2
  AbNormal: 120, Normal: 232
  AbNormal Ratio: 0.34, Normal Ratio: 0.66
Model Suffix Value: 3
  AbNormal: 336, Normal: 704
  AbNormal Ratio: 0.32, Normal Ratio: 0.68
Model Suffix Value: 4
  AbNormal: 12, Normal: 52
  AbNormal Ratio: 0.19, Normal Ratio: 0.81
Model Suffix Value: 5
  AbNormal: 56, Normal: 88
  AbNormal Ratio: 0.39, Normal Ratio: 0.61
Model Suffix Value: 6
  AbNormal: 0, Normal: 16
  AbNormal Ratio: 0.00, Normal Ratio: 1.00


In [ ]:
submission['target'].value_counts()

target
Normal      11293
AbNormal     6068
Name: count, dtype: int64

In [ ]:
# df_AbNormal = result[result['target'] == 'AbNormal']
# df_AbNormal

In [ ]:
# pd.set_option('display.max_rows', None)
print('Feature Importances:')
print(feature_importance_df)

Feature Importances:
                                               Feature  Importance
217                                Workorder_AutoClave    9.035138
2                                        Workorder_Dam    6.836231
237                                    Workorder_Fill1    5.455477
332                                    Workorder_Fill2    4.581437
230                  Chamber Temp. Unit Time_AutoClave    2.660471
..                                                 ...         ...
225                 2nd Pressure Judge Value_AutoClave    0.000000
60   HEAD NORMAL COORDINATE X AXIS(Stage2) Unit Tim...    0.000000
222                 1st Pressure Judge Value_AutoClave    0.000000
61   HEAD NORMAL COORDINATE X AXIS(Stage2) Judge Va...    0.000000
454                         WorkMode Judge Value_Fill2    0.000000

[455 rows x 2 columns]


In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

def plot_feature_importance(importance, names):
    feature_importance = np.array(importance)
    feature_names = np.array(names)

    data = {'feature_names': feature_names, 'feature_importance': feature_importance}
    fi_df = pd.DataFrame(data)

    fi_df.sort_values(by=['feature_importance'], ascending=False, inplace=True)

    plt.figure(figsize=(100, 100))
    sns.barplot(x=fi_df['feature_importance'], y=fi_df['feature_names'])

    plt.xlabel('Feature Importance')
    plt.ylabel('Feature Names')
    plt.title('Feature Importance')
    plt.show()

# 함수 사용 예시
plot_feature_importance(feature_importance, x.columns)
